In [105]:
import nltk

In [106]:
from nltk.corpus import genesis

In [107]:
genesis_words = genesis.words()

In [108]:
def filter_letter(let):

    if ord('a') <= ord(let) <= ord('z'):
        return True
    
    else:
        return False

In [109]:
def make_blocks(word_list,block_size):
    word_str = "".join(word_list)
    new_str = ""
    blocked_arr = []



    for i in range(0,len(word_str)):
        
        let = word_str[i].lower()
        if filter_letter(let):
            new_str += let
        else:
            pass
    
    del word_str

    for i in range(0, len(new_str), block_size):
        block = new_str[i:i+block_size]
        
        if len(block) == block_size:
            blocked_arr.append(block)
        else:
            diff = block_size - len(block)
            padded_block = block + "x" * diff
            blocked_arr.append(padded_block)

    return blocked_arr

In [110]:
pt_blocks = make_blocks(genesis_words,8)

print(pt_blocks[:10])

['inthebeg', 'inninggo', 'dcreated', 'theheave', 'nandthee', 'arthandt', 'heearthw', 'aswithou', 'tformand', 'voidandd']


In [111]:
unique_chars = set()

for word in pt_blocks:

    for let in word:

        if not let in unique_chars:
            unique_chars.add(let)


print(len(unique_chars))


 

26


# DES

In [112]:
from Crypto.Cipher import DES
from Crypto.Random import get_random_bytes
from Crypto.Util.Padding import pad, unpad
import base64

password = "alpha"  # plaintext
key = b'\xe8 \xdez\xa6.\x9b\t'
cipher = DES.new(key, DES.MODE_ECB)

# encryption
padding = pad(password.encode(), 8)
enc_pass = base64.b64encode(cipher.encrypt(padding))

print(enc_pass)

b'uOUt/SBHH3E='


In [113]:
cipher.encrypt(padding)

b'\xb8\xe5-\xfd G\x1fq'

In [114]:
ct_blocks = []


unique_chars = set()





print(len(unique_chars))
for m in pt_blocks:
    # m = bytes(m,'utf-8')
    # encryption
    padding = pad(m.encode(), 8)
    enc_pass = base64.b64encode(cipher.encrypt(padding))  # cipher text
    enc_pass = enc_pass.decode('utf-8')  # cipher text
    ct_blocks.append(enc_pass)

    for let in m:

        if not let in unique_chars:
            unique_chars.add(let)


print(len(unique_chars))


0
26


In [115]:
print(set(pt_blocks))
print(set(ct_blocks))

{'rdsmenof', 'bovidhav', 'llesanan', 'heseaand', 'eenmeand', 'porventu', 'lnichtau', 'kenmendu', 'nomnoass', 'shedonot', 'sorrowto', 'rundavpe', 'mtodosos', 'rsomhava', 'senlasse', 'nnuidagi', 'theredto', 'eetcelaf', 'uconcert', 'nmitjoos', 'vattulle', 'uredenmi', 'emgeldef', 'gertolvh', 'nhdenhau', 'ardwheni', 'esieberm', 'enochvar', 'emnahorg', 'tjakobva', 'settguda', 'igergnad', 'ousceuxq', 'hhehadna', 'ejacentr', 'chinarvo', 'ewithmyf', 'angryand', 'achnorde', 'derfuhrf', 'adschlep', 'sallaita', 'bdemeura', 'uefaland', 'rnaochdo', 'mickessg', 'chhansad', 'akobines', 'astomana', 'andspake', 'illuiarr', 'llbeaswe', 'lljagutk', 'hshebaan', 'dasander', 'ahantehr', 'llocksin', 'nshandbu', 'wherehei', 'usjaakob', 'llstofts', 'gepourdt', 'patiinel', 'eravecmo', 'stttesch', 'nrenprof', 'pepourqu', 'eftcuzde', 'rsfrndeo', 'eseriusa', 'skjutitu', 'ploopuca', 'avontade', 'odoldage', 'nemaanpl', 'madaijaw', 'oiseauxt', 'asviehei', 'schobalz', 'ismeinso', 'gundsota', 'heepshea', 'andagain', 'nn

In [116]:
ct_set = set("".join(ct_blocks))
pt_set = set("".join(pt_blocks))

In [117]:
print(len(pt_set),len(ct_set))

26 65


In [118]:
ps_str = "".join(sorted(pt_set))

cs_str = "".join(sorted(ct_set))

In [119]:
p_ord_ls = [ord(i) for i in ps_str]
c_ord_ls = [ord(i) for i in cs_str]

In [120]:
print(max(p_ord_ls), min(p_ord_ls))
print(max(c_ord_ls), min(c_ord_ls))

122 97
122 43


In [121]:
unique_lens = []

for ct in ct_blocks:
    if not len(ct) in unique_lens:
        unique_lens.append(len(ct))
    else:
        pass

print(unique_lens)

[24]


# Seq2Seq model implementation

In [134]:
import numpy as np
import keras
from keras.models import Sequential
from keras.layers import Dense,InputLayer

In [123]:
batch_size = 64
num_samples = 137957
latent_dim = 512
epochs = 100

In [124]:
input_texts = pt_blocks
target_texts = ct_blocks

In [125]:
# Start token \t
# end token \n

input_characters = set()
target_characters = set()
for i in range(len(input_texts)):

    input_texts[i] = input_texts[i] + '\n'
    
    for char in input_texts[i]:
        if char not in input_characters:
            input_characters.add(char)



for j in range(len(target_texts)):
    target_texts[j] = '\t' + target_texts[j] + '\n'
    
    for char in target_texts[j]:
        if char not in target_characters:
            target_characters.add(char)

In [126]:
unique_chars = set()

for word in pt_blocks:

    for let in word:

        if not let in unique_chars:
            unique_chars.add(let)


print(len(unique_chars))

27


In [127]:
input_characters.add(' ')
target_characters.add(' ')
input_characters = sorted(list(input_characters))
target_characters = sorted(list(target_characters))

num_encoder_tokens = len(input_characters)
num_decoder_tokens = len(target_characters)

max_encoder_seq_length = max([len(txt) for txt in input_texts])
max_decoder_seq_length = max([len(txt) for txt in target_texts])


print("Number of samples:", len(input_texts))
print("Number of unique input tokens:", num_encoder_tokens)
print("Number of unique output tokens:", num_decoder_tokens)
print("Max sequence length for inputs:", max_encoder_seq_length)
print("Max sequence length for outputs:", max_decoder_seq_length)

Number of samples: 134339
Number of unique input tokens: 28
Number of unique output tokens: 68
Max sequence length for inputs: 9
Max sequence length for outputs: 26


In [128]:
input_token_index = dict([(char, i)
                         for i, char in enumerate(input_characters)])
target_token_index = dict([(char, i)
                          for i, char in enumerate(target_characters)])

encoder_input_data = np.zeros(
    (len(input_texts), max_encoder_seq_length, num_encoder_tokens),
    dtype="float32",
)
decoder_input_data = np.zeros(
    (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype="float32",
)
decoder_target_data = np.zeros(
    (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
    dtype="float32",
)

In [129]:
encoder_input_data.shape

(134339, 9, 28)

In [130]:
for i, (input_text, target_text) in enumerate(zip(input_texts, target_texts)):
    for t, char in enumerate(input_text):
        encoder_input_data[i, t, input_token_index[char]] = 1.0
    encoder_input_data[i, t + 1:, input_token_index[" "]] = 1.0
    for t, char in enumerate(target_text):
        # decoder_target_data is ahead of decoder_input_data by one timestep
        decoder_input_data[i, t, target_token_index[char]] = 1.0
        if t > 0:
            # decoder_target_data will be ahead by one timestep
            # and will not include the start character.
            decoder_target_data[i, t - 1, target_token_index[char]] = 1.0
    decoder_input_data[i, t + 1:, target_token_index[" "]] = 1.0
    decoder_target_data[i, t:, target_token_index[" "]] = 1.0

In [131]:
print(encoder_input_data.shape)
print(decoder_target_data.shape)

(134339, 9, 28)
(134339, 26, 68)


In [132]:
# Define an input sequence and process it.
encoder_inputs = keras.Input(shape=(None, num_encoder_tokens))
encoder = keras.layers.LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)

# We discard `encoder_outputs` and only keep the states.
encoder_states = [state_h, state_c]

# Set up the decoder, using `encoder_states` as initial state.
decoder_inputs = keras.Input(shape=(None, num_decoder_tokens))

# We set up our decoder to return full output sequences,
# and to return internal states as well. We don't use the
# return states in the training model, but we will use them in inference.
decoder_lstm = keras.layers.LSTM(
    latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(
    decoder_inputs, initial_state=encoder_states)
decoder_dense = keras.layers.Dense(num_decoder_tokens, activation="softmax")
decoder_outputs = decoder_dense(decoder_outputs)

# Define the model that will turn
# `encoder_input_data` & `decoder_input_data` into `decoder_target_data`
model = keras.Model([encoder_inputs, decoder_inputs], decoder_outputs)

In [142]:
print(encoder_input_data.shape)
print(num_encoder_tokens)

(134339, 9, 28)
28


In [147]:
fat_shallow_model = Sequential(
    [
        InputLayer(input_shape=(None,num_encoder_tokens)),
        # Dense(16, activation='relu'),
        # Dense(16, activation='relu'),
        # Dense(16, activation='relu'),
        # Dense(16, activation='relu')
        Dense(num_decoder_tokens,activation="softmax")
    ]
)

fat_shallow_model.compile(
    optimizer="rmsprop", loss="mse", metrics=["accuracy"]
)

pred = fat_shallow_model.predict(encoder_input_data[:2])

# fat_shallow_model.fit(
#     encoder_input_data,
#     decoder_target_data,
#     batch_size=batch_size,
#     epochs=epochs,
#     validation_split=0.2,
# )

print(pred.shape)
print(decoder_target_data.shape)

1/1 [==============================] - 0s 51ms/step
(2, 9, 68)
(134339, 26, 68)


In [133]:
model.compile(
    optimizer="rmsprop", loss="categorical_crossentropy", metrics=["accuracy"]
)
model.fit(
    [encoder_input_data, decoder_input_data],
    decoder_target_data,
    batch_size=batch_size,
    epochs=epochs,
    validation_split=0.2,
)
# Save model
model.save("s2s_model.keras")

Epoch 1/100
1680/1680 [==============================] - 180s 106ms/step - loss: 1.8468 - accuracy: 0.5601 - val_loss: 1.7175 - val_accuracy: 0.5855
Epoch 2/100
1680/1680 [==============================] - 178s 106ms/step - loss: 1.7182 - accuracy: 0.5845 - val_loss: 1.7161 - val_accuracy: 0.5854
Epoch 3/100
1680/1680 [==============================] - 178s 106ms/step - loss: 1.7105 - accuracy: 0.5855 - val_loss: 1.7092 - val_accuracy: 0.5854
Epoch 4/100
1564/1680 [==========================>...] - ETA: 10s - loss: 1.7091 - accuracy: 0.5858

KeyboardInterrupt: 